In [423]:
import folium as fl
import pandas as pd
import geopandas as gpd
from hdx.api.configuration import Configuration
from hdx.data.resource import Resource
import json
import itertools
from shapely.geometry import Polygon,MultiPolygon
import time
import numpy as np
from gadm import GADMDownloader

In [424]:
# Initialize the GADMDownloader with the specified version (in this case, version 4.0)
downloader = GADMDownloader(version="4.0")

# Define the country name for which you want to retrieve administrative boundary data
country_name = "IND"

# Specify the administrative level you are interested in (e.g., 1 for districts or provinces)
ad_level = 2

# Retrieve the geospatial data for the selected country and administrative level
copygdf = downloader.get_shape_data_by_country_name(country_name=country_name, ad_level=ad_level)

In [425]:
popdf = pd.read_csv('./ppp_IND_2020_1km_Aggregated_UNadj.csv')

In [426]:
popdf = popdf.reset_index()
popdf.head()

index          X          Y         Z
0      0  77.827916  35.503750  1.003104
1      1  77.836250  35.503750  0.977130
2      2  77.844583  35.503750  0.324360
3      3  77.819583  35.495417  0.826524
4      4  77.827916  35.495417  0.328031

In [427]:
popdf.columns = ['ID','xcoord','ycoord','population']
popdf['population'] = popdf['population'].astype(int)
pop = gpd.GeoDataFrame(popdf,geometry=gpd.points_from_xy(x=popdf.xcoord, y=popdf.ycoord))

In [428]:
print('Total Population:',round(pop['population'].sum()/1000000,2),'million')

Total Population: 1378.0 million


In [429]:
copygdf

ID_0 COUNTRY               NAME_1 NL_NAME_1         ID_2  \
0    IND   India  Andaman and Nicobar              IND.1.1_1   
1    IND   India  Andaman and Nicobar              IND.1.2_1   
2    IND   India  Andaman and Nicobar              IND.1.3_1   
3    IND   India       Andhra Pradesh              IND.2.1_1   
4    IND   India       Andhra Pradesh              IND.2.2_1   
..   ...     ...                  ...       ...          ...   
661  IND   India          West Bengal            IND.36.16_1   
662  IND   India          West Bengal            IND.36.17_1   
663  IND   India          West Bengal            IND.36.18_1   
664  IND   India          West Bengal            IND.36.19_1   
665  IND   India          West Bengal            IND.36.20_1   

                       NAME_2             VARNAME_2 NL_NAME_2    TYPE_2  \
0             Nicobar Islands                                  District   
1    North and Middle Andaman                                  District   
2               South Andaman                                  District   
3                   Anantapur  Anantpur, Ananthapur            District   
4                    Chittoor       Chitoor|Chittor            District   
..                        ...                   ...       ...       ...   
661        Pashchim Medinipur     Paschim Medinipur            District   
662           Purba Medinipur       Purba Medinipur            District   
663                  Puruliya                                  District   
664         South 24 Parganas                                  District   
665            Uttar Dinajpur                                  District   

    ENGTYPE_2 CC_2    HASC_2  \
0    District       IN.AN.NI   
1    District       IN.AN.NM   
2    District       IN.AN.SA   
3    District       IN.AD.AN   
4    District       IN.AD.CH   
..        ...  ...       ...   
661  District       IN.WB.WM   
662  District       IN.WB.EM   
663  District       IN.WB.PU   
664  District       IN.WB.PS   
665  District       IN.WB.UD   

                                              geometry  
0    MULTIPOLYGON (((93.78988 6.85201, 93.79015 6.8...  
1    MULTIPOLYGON (((92.84441 12.14969, 92.84466 12...  
2    MULTIPOLYGON (((92.52111 10.89694, 92.52306 10...  
3    MULTIPOLYGON (((77.846 13.92832, 77.83012 13.9...  
4    MULTIPOLYGON (((78.54555 12.74391, 78.55031 12...  
..                                                 ...  
661  MULTIPOLYGON (((86.72535 22.2135, 86.73376 22....  
662  MULTIPOLYGON (((87.48177 21.60942, 87.48176 21...  
663  MULTIPOLYGON (((85.87758 23.47586, 85.89125 23...  
664  MULTIPOLYGON (((88.02139 21.57111, 88.02111 21...  
665  MULTIPOLYGON (((88.45433 25.663, 88.45429 25.6...  

[666 rows x 13 columns]

In [638]:
gdf = copygdf

## Select required area

In [639]:
region_name, state_name = 'Bilaspur', 'Himachal Pradesh'

In [640]:
gdf['NAME_1'].unique()

array(['Andaman and Nicobar', 'Andhra Pradesh', 'Arunachal Pradesh',
       'Assam', 'Bihar', 'Chandigarh', 'Chhattisgarh',
       'Dadra and Nagar Haveli', 'Daman and Diu', 'Goa', 'Gujarat',
       'Haryana', 'Himachal Pradesh', 'Jammu and Kashmir', 'Jharkhand',
       'Karnataka', 'Kerala', 'Lakshadweep', 'Madhya Pradesh',
       'Maharashtra', 'Manipur', 'Meghalaya', 'Mizoram', 'Nagaland',
       'NCT of Delhi', 'Odisha', 'Puducherry', 'Punjab', 'Rajasthan',
       'Sikkim', 'Tamil Nadu', 'Telangana', 'Tripura', 'Uttar Pradesh',
       'Uttarakhand', 'West Bengal'], dtype=object)

In [641]:
gdf = gdf[gdf['NAME_1'] == state_name]

In [642]:
gdf['NAME_2'].unique()

array(['Bilaspur', 'Chamba', 'Hamirpur', 'Kangra', 'Kinnaur', 'Kullu',
       'Lahul & Spiti', 'Mandi', 'Shimla', 'Sirmaur', 'Solan', 'Una'],
      dtype=object)

In [643]:
gdf = gdf[gdf['NAME_2'] == region_name]

In [644]:
selected_gdf = gdf

In [645]:
from IPython.display import display, HTML

# Inject custom CSS to prevent overflow and ensure the map container fits properly
display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 60% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 40% !important; /* Full height within the container */
        }
    </style>
"""))

# Create a Folium map with a temporary zoom level
m = fl.Map(zoom_start=1, tiles="OpenStreetMap")

# Get the bounds (bounding box) of the geometries in selected_gdf
bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]

# Set the map's location and zoom to fit the bounds
m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

# Iterate through each row in the geospatial data (gdf) representing administrative boundaries
for _, r in selected_gdf.iterrows():
    # Simplify the geometry of the current boundary with a specified tolerance
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)
    # Convert the simplified geometry to JSON format
    geo_j = sim_geo.to_json()

    # Create a GeoJson layer from the JSON geometry, and style it with a red fill color
    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "red"})

    # Add a popup with the NAME_3 attribute (administrative region name) to the GeoJson layer
    fl.Popup(r["NAME_2"]).add_to(geo_j)

    # Add the styled GeoJson layer to the Folium map (m)
    geo_j.add_to(m)

# Display the map wrapped in a custom div to control size
display(HTML('<div class="map-container">' + m._repr_html_() + '</div>'))


## Population dataframe

In [646]:
pop = pop.set_crs(selected_gdf.crs)

### Population distribution in the area of interest

In [647]:
population_aoi = gpd.sjoin(pop, selected_gdf, predicate='within')
print(f'Total Population (Area of Interest - {selected_gdf}):',round(population_aoi['population'].sum()))

Total Population (Area of Interest -     ID_0 COUNTRY            NAME_1 NL_NAME_1        ID_2    NAME_2 VARNAME_2  \
186  IND   India  Himachal Pradesh            IND.13.1_1  Bilaspur             

    NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
186            District  District       IN.HP.BI   

                                              geometry  
186  MULTIPOLYGON (((76.79752 31.42692, 76.80199 31...  ): 500448


In [648]:
quartile_labels = [0.1, 0.25, 0.5, 1.0]
population_aoi['opacity'] = pd.qcut(population_aoi['population'], 4, labels=quartile_labels)

In [649]:
print(population_aoi.head())

            ID     xcoord     ycoord  population                   geometry  \
210690  210690  76.677916  31.595417         512  POINT (76.67792 31.59542)   
210691  210691  76.686250  31.595417         510  POINT (76.68625 31.59542)   
210692  210692  76.694583  31.595417         491  POINT (76.69458 31.59542)   
210693  210693  76.702916  31.595417         508  POINT (76.70292 31.59542)   
211189  211189  76.627916  31.587083         354  POINT (76.62792 31.58708)   

        index_right ID_0 COUNTRY            NAME_1 NL_NAME_1        ID_2  \
210690          186  IND   India  Himachal Pradesh            IND.13.1_1   
210691          186  IND   India  Himachal Pradesh            IND.13.1_1   
210692          186  IND   India  Himachal Pradesh            IND.13.1_1   
210693          186  IND   India  Himachal Pradesh            IND.13.1_1   
211189          186  IND   India  Himachal Pradesh            IND.13.1_1   

          NAME_2 VARNAME_2 NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HAS

In [650]:
print(population_aoi.describe())

                  ID       xcoord       ycoord   population  index_right
count    1545.000000  1545.000000  1545.000000  1545.000000       1545.0
mean   224151.906796    76.661568    31.375206   323.914563        186.0
std      5559.510937     0.117349     0.088156   226.190731          0.0
min    210690.000000    76.386250    31.220417     6.000000        186.0
25%    220647.000000    76.586250    31.303750   182.000000        186.0
50%    224317.000000    76.669583    31.370417   259.000000        186.0
75%    228644.000000    76.744583    31.428750   411.000000        186.0
max    234307.000000    76.911250    31.595417  2577.000000        186.0


In [651]:
import folium as fl
import geopandas as gpd

# Create a base map
m = fl.Map(zoom_start=12, tiles="OpenStreetMap")

# Get the bounds (bounding box) of the geometries in selected_gdf
bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]

# Set the map's location and zoom to fit the bounds
m.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

# Iterate through each row in the geospatial data representing the boundary of Plymouth
for _, r in selected_gdf.iterrows():
    # Simplify the geometry of the current boundary with a specified tolerance
    sim_geo = gpd.GeoSeries(r["geometry"]).simplify(tolerance=0.0001)
    # Convert the simplified geometry to JSON format
    geo_j = sim_geo.to_json()

    # Create a GeoJson layer from the JSON geometry, and style it with a light fill color
    geo_j = fl.GeoJson(data=geo_j, style_function=lambda x: {"fillColor": "#ffffcc", "color": "black", "weight": 2, "fillOpacity": 0.3})

    # # Add a popup with the NAME_2 attribute (administrative region name) to the GeoJson layer
    # fl.Popup(r["NAME_2"]).add_to(geo_j)

    # Add the styled GeoJson layer to the Folium map (m)
    geo_j.add_to(m)

import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

# Assuming population_aoi DataFrame is already defined and contains the population data
# Define the colormap and normalization
vmin = np.log1p(population_aoi['population'].min()+1)  # Minimum population value
vmax = np.log1p(population_aoi['population'].max())  # Maximum population value

# Create a colormap
cmap = plt.get_cmap("OrRd")  # You can choose any colormap you prefer
norm = mcolors.LogNorm(vmin=vmin, vmax=vmax)

# Add population data from population_aoi as gradient color for each point
for _, row in population_aoi.iterrows():
    # Get the coordinates
    coords = (row['ycoord'], row['xcoord'])  # Latitude first, then Longitude

    # Define a gradient color based on population
    population_value = row['population']
    if population_value > 0:
        fill_color = mcolors.rgb2hex(cmap(norm(np.log1p(population_value)))[:3])  # Convert to hex color
    else:
        fill_color = "#ffb68700"  # Default color for zero population

    # Create a small circle to represent the population point with gradient color
    fl.CircleMarker(
        location=coords,
        radius=2*max(2, np.log1p(population_value) / 5),  # Adjust the size based on population
        color=fill_color,
        fill=True,
        fill_opacity=0.7,
        opacity=0.4,  # Set border opacity
        popup=f"Population: {population_value}"  # Optional: show population value in popup
    ).add_to(m)
    
# Display the map
m

In [652]:
import requests

overpass_url = "https://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
area["ISO3166-1"="IN"]["admin_level"="2"];
(node["amenity"="hospital"](area);
 way["amenity"="hospital"](area);
 rel["amenity"="hospital"](area);
);
out center;
"""
response = requests.get(overpass_url, params={'data': overpass_query})
data = response.json()

In [653]:
df_hospitals = pd.DataFrame(data['elements'])

df_hospitals['name'] = df_hospitals['tags'].apply(lambda x:x['name'] if 'name' in list(x.keys()) else None)

df_hospitals = df_hospitals[['id','lat','lon','name']].drop_duplicates()

df_health_osm = df_hospitals
df_health_osm = gpd.GeoDataFrame(df_health_osm, geometry=gpd.points_from_xy(df_health_osm.lon, df_health_osm.lat))
df_health_osm = df_health_osm[['id','name','geometry']]

print('Number of hospitals extracted:',len(df_health_osm))
df_health_osm = df_health_osm.set_crs(selected_gdf.crs)

Number of hospitals extracted: 49375


In [654]:
selected_hosp = gpd.sjoin(df_health_osm, selected_gdf, predicate='within')
print('Number of hospitals in AOI (',selected_gdf,'):',len(selected_hosp))

Number of hospitals in AOI (     ID_0 COUNTRY            NAME_1 NL_NAME_1        ID_2    NAME_2 VARNAME_2  \
186  IND   India  Himachal Pradesh            IND.13.1_1  Bilaspur             

    NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HASC_2  \
186            District  District       IN.HP.BI   

                                              geometry  
186  MULTIPOLYGON (((76.79752 31.42692, 76.80199 31...   ): 19


In [655]:
selected_hosp.head()

id                       name                   geometry  \
1253  3043556695  Civil Hospital, Ghumarwin   POINT (76.7115 31.43776)   
1254  3043559259           Rainbow Hospital  POINT (76.71051 31.43761)   
1255  3043562381             Shiva Hospital  POINT (76.71541 31.43661)   
1256  3043566806           Bharati Hospital  POINT (76.71213 31.44185)   
1258  3043579091    Vyas Hospital, Bilaspur   POINT (76.7474 31.35971)   

      index_right ID_0 COUNTRY            NAME_1 NL_NAME_1        ID_2  \
1253          186  IND   India  Himachal Pradesh            IND.13.1_1   
1254          186  IND   India  Himachal Pradesh            IND.13.1_1   
1255          186  IND   India  Himachal Pradesh            IND.13.1_1   
1256          186  IND   India  Himachal Pradesh            IND.13.1_1   
1258          186  IND   India  Himachal Pradesh            IND.13.1_1   

        NAME_2 VARNAME_2 NL_NAME_2    TYPE_2 ENGTYPE_2 CC_2    HASC_2  
1253  Bilaspur                      District  District       IN.HP.BI  
1254  Bilaspur                      District  District       IN.HP.BI  
1255  Bilaspur                      District  District       IN.HP.BI  
1256  Bilaspur                      District  District       IN.HP.BI  
1258  Bilaspur                      District  District       IN.HP.BI

In [656]:
# Iterate through each row in the selected_hosp GeoDataFrame
for _, row in selected_hosp.iterrows():
    # Get the coordinates
    coords = (row.geometry.y, row.geometry.x)  # Latitude first, then Longitude

    # Get the hospital name
    hospital_name = row['name'] if row['name'] else "Unnamed Hospital"

    # Create a circle marker for each hospital
    fl.CircleMarker(
        location=coords,
        radius=3,  # Adjust the size as needed
        color='black',
        fill=True,
        fill_color='black',
        fill_opacity=0.7,
        popup=hospital_name
    ).add_to(m)

# Display the map
m

In [657]:
ors_api_key = '5b3ce3597851110001cf62482253ee95a235474d85c4a81fedd541cd'

In [659]:
def get_isochrone_osm (each_hosp):
  body = {"locations":[[each_hosp.x,each_hosp.y]],"range":[1800],"range_type":'time'}
  headers = {
      'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
      'Authorization': ors_api_key,
      'Content-Type': 'application/json; charset=utf-8'
  }
  call = requests.post('https://api.openrouteservice.org/v2/isochrones/driving-car', json=body, headers=headers)
  print(call.text)
  geom = (json.loads(call.text)['features'][0]['geometry'])
  polygon_geom = Polygon(geom['coordinates'][0])
  time.sleep(3)
  return polygon_geom

selected_hosp['cachment_area'] = selected_hosp['geometry'].apply(get_isochrone_osm)

{
    "error": "Quota exceeded"
}


KeyError: 'features'

In [ ]:
def get_pop_count(cachment,pop_data):
  pop_access = pop_data[pop_data.within(cachment)]
  id_values = (pop_access['ID'].values)
  pop_with_access = (pop_access['population'].sum().round())
  return id_values,pop_with_access

selected_hosp['id_with_access'], selected_hosp['pop_with_access'] = zip(*selected_hosp['cachment_area'].apply(get_pop_count, pop_data=population_aoi))

In [ ]:
list_ids_access = list(selected_hosp['id_with_access'].values)
list_ids_access = list(itertools.chain.from_iterable(list_ids_access))
pop_with_access = population_aoi[population_aoi['ID'].isin(list_ids_access)]
pop_without_access = population_aoi[~population_aoi['ID'].isin(list_ids_access)]

print('Population with Access:',round(pop_with_access['population'].sum()*100/population_aoi['population'].sum(),2),'%')

Population with Access: 93.98 %


In [613]:
from IPython.display import display, HTML
import folium as fl

# Inject custom CSS to prevent overflow and ensure the map container fits properly
display(HTML("""
    <style>
        .map-container {
            width: 60% !important;  /* Adjust width as needed */
            height: 40% !important; /* Adjust height as needed */
            margin: 0 auto;         /* Center the map */
            border: 2px solid black; /* Optional: to visualize the map container */
        }
        .leaflet-container {
            width: 100% !important;  /* Make sure the leaflet map takes up the full width of the container */
            height: 100% !important; /* Full height within the container */
        }
    </style>
"""))

# Create a Folium map with a temporary zoom level
folium_map = fl.Map(zoom_start=1, tiles="OpenStreetMap")

# Get the bounds (bounding box) of the geometries in selected_gdf
bounds = selected_gdf.total_bounds  # Returns [minx, miny, maxx, maxy]

# Set the map's location and zoom to fit the bounds
folium_map.fit_bounds([[bounds[1], bounds[0]], [bounds[3], bounds[2]]])

# Add a title to the map
folium_map.get_root().html.add_child(fl.Element(f'<h3 style="text-align:center;"><b>Healthcare access distribution</b></h3>'))
folium_map.get_root().html.add_child(fl.Element(f'<h3 style="text-align:center;"><b>{region_name, state_name}</b></h3>'))

# Add a legend to the bottom right corner
legend_html = """
<div style="position: fixed; 
            bottom: 50px; right: 50px; 
            background-color: white; 
            padding: 20px;
            border:2px solid grey;
            z-index:9999;">
    <b>Legend</b><br>
    <i style="color:red;font-size:20px;">&#9679;</i> Population with less access<br>
    <i style="color:green;font-size:20px;">&#9679;</i> Population with high access
</div>
"""
folium_map.get_root().html.add_child(fl.Element(legend_html))

geo_adm = fl.GeoJson(data=selected_gdf.iloc[0]['geometry'],style_function=lambda x:{'color': 'orange'})
geo_adm.add_to(folium_map)

for i in range(0,len(selected_hosp)):
    fl.Marker([selected_hosp.iloc[i]['geometry'].y, selected_hosp.iloc[i]['geometry'].x],
              popup=selected_hosp.iloc[i]['name']).add_to(folium_map)

# This loop is not necessary if pop_without_access is empty
for i in range(0,len(pop_without_access)):
  fl.CircleMarker(
        location=[pop_without_access.iloc[i]['ycoord'], pop_without_access.iloc[i]['xcoord']],
        radius=3,
        color=None,
        fill=True,
        fill_color='red',
        fill_opacity=pop_without_access.iloc[i]['opacity']).add_to(folium_map)

for i in range(0,len(pop_with_access)):
  fl.CircleMarker(
        location=[pop_with_access.iloc[i]['ycoord'], pop_with_access.iloc[i]['xcoord']],
        radius=3,
        color=None,
        fill=True,
        fill_color='green',
        fill_opacity=pop_with_access.iloc[i]['opacity']).add_to(folium_map)

folium_map

In [614]:
folium_map.save(f'{region_name}_{state_name}_access.html') 